In [1]:
import pandas as pd
import os
import shutil
from rapidfuzz import fuzz
from datetime import datetime, timezone

In [2]:
def check_for_duplicate_players_by_name(data_directory, seasons):
    duplicate_players = {}

    for season in seasons:
        season_path = os.path.join(data_directory, season)
        player_idlist_path = os.path.join(season_path, "player_idlist.csv")
        
        if not os.path.exists(player_idlist_path):
            print(f"player_idlist.csv not found for season: {season}")
            continue
        
        try:
            player_idlist = pd.read_csv(player_idlist_path)
            duplicates = player_idlist.duplicated(subset=['first_name', 'second_name'], keep=False)
            duplicate_names = player_idlist.loc[duplicates, ['first_name', 'second_name']].drop_duplicates()

            if not duplicate_names.empty:
                duplicate_players[season] = duplicate_names
                print(f"Found duplicate names in season {season}:")
                print(duplicate_names)
            else:
                print(f"No duplicate names found in season {season}.")
        
        except Exception as e:
            print(f"Error checking duplicates for season {season}: {e}")

    return duplicate_players

data_directory = "Fantasy-Premier-League/data"
seasons = ["2020-21", "2021-22", "2022-23", "2023-24", "2024-25"]
duplicates_by_name = check_for_duplicate_players_by_name(data_directory, seasons)

Found duplicate names in season 2020-21:
    first_name second_name
381        Ben      Davies
Found duplicate names in season 2021-22:
    first_name second_name
113     Álvaro   Fernández
397        Ben      Davies
Found duplicate names in season 2022-23:
    first_name second_name
462        Ben      Davies
No duplicate names found in season 2023-24.
No duplicate names found in season 2024-25.


In [3]:
# We found the duplicates to Ben Davies in seasons 2020-21, 2021-22 and 2022-23 and Alvaro Fernandez in 2021-22.
# We will keep the Tottenham Hotspurs Ben Davies as he is also in the current season but we can safely remove
# both Alvaro Fernandezes and the Liverpool Ben Davies since they had almost no minutes during their Premier 
# League time
def remove_players_and_folders(data_directory, players_to_remove):
    for player in players_to_remove:
            season = player["season"]
            player_id = player["id"]
            first_name = player["first_name"]
            second_name = player["second_name"]

            season_path = os.path.join(data_directory, season)
            player_idlist_path = os.path.join(season_path, "player_idlist.csv")
            players_folder_path = os.path.join(season_path, "players")

            if not os.path.exists(player_idlist_path):
                print(f"player_idlist.csv not found for season {season}. Skipping.")
                continue

            try:
                # Remove from player_idlist.csv
                player_idlist = pd.read_csv(player_idlist_path)

                # Find matching player row
                matching_rows = player_idlist[
                    (player_idlist["id"] == player_id) &
                    (player_idlist["first_name"] == first_name) &
                    (player_idlist["second_name"] == second_name)
                ]

                if not matching_rows.empty:
                    # Remove the player from the DataFrame
                    player_idlist = player_idlist.drop(matching_rows.index)
                    # Save back to CSV
                    player_idlist.to_csv(player_idlist_path, index=False)
                    print(f"Removed {first_name} {second_name} (ID: {player_id}) from {player_idlist_path}.")
                else:
                    print(f"Player {first_name} {second_name} (ID: {player_id}) not found in {player_idlist_path}. Skipping.")

                # Remove player folder
                player_folder_name = f"{first_name}_{second_name}_{player_id}"
                player_folder_path = os.path.join(players_folder_path, player_folder_name)
                if os.path.exists(player_folder_path):
                    shutil.rmtree(player_folder_path)
                    print(f"Removed folder: {player_folder_path}")
                else:
                    print(f"Folder {player_folder_path} not found. Skipping.")

            except Exception as e:
                print(f"Error processing {first_name} {second_name} (ID: {player_id}) for season {season}: {e}")

    # Example usage
data_directory = "Fantasy-Premier-League/data"
players_to_remove = [
        {"season": "2020-21", "first_name": "Ben", "second_name": "Davies", "id": 653},
        {"season": "2021-22", "first_name": "Álvaro", "second_name": "Fernández", "id": 556},
        {"season": "2021-22", "first_name": "Álvaro", "second_name": "Fernández", "id": 728},
        {"season": "2023-24", "first_name": "Álvaro", "second_name": "Fernández Carreras", "id": 380},
        {"season": "2021-22", "first_name": "Ben", "second_name": "Davies", "id": 248},
        {"season": "2022-23", "first_name": "Ben", "second_name": "Davies", "id": 499},
]

remove_players_and_folders(data_directory, players_to_remove)

Removed Ben Davies (ID: 653) from Fantasy-Premier-League/data/2020-21/player_idlist.csv.
Removed folder: Fantasy-Premier-League/data/2020-21/players/Ben_Davies_653
Removed Álvaro Fernández (ID: 556) from Fantasy-Premier-League/data/2021-22/player_idlist.csv.
Removed folder: Fantasy-Premier-League/data/2021-22/players/Álvaro_Fernández_556
Removed Álvaro Fernández (ID: 728) from Fantasy-Premier-League/data/2021-22/player_idlist.csv.
Removed folder: Fantasy-Premier-League/data/2021-22/players/Álvaro_Fernández_728
Removed Álvaro Fernández Carreras (ID: 380) from Fantasy-Premier-League/data/2023-24/player_idlist.csv.
Removed folder: Fantasy-Premier-League/data/2023-24/players/Álvaro_Fernández Carreras_380
Removed Ben Davies (ID: 248) from Fantasy-Premier-League/data/2021-22/player_idlist.csv.
Removed folder: Fantasy-Premier-League/data/2021-22/players/Ben_Davies_248
Removed Ben Davies (ID: 499) from Fantasy-Premier-League/data/2022-23/player_idlist.csv.
Removed folder: Fantasy-Premier-Leagu

In [4]:
# First let's get each player position and id for the season
def process_season_data(data_directory, seasons):
    for season in seasons:
        season_path = os.path.join(data_directory, season)

        if os.path.isdir(season_path):
            player_idlist_path = os.path.join(season_path, "player_idlist.csv")
            cleaned_players_path = os.path.join(season_path, "cleaned_players.csv")
            output_file_path = os.path.join(season_path, "processed_players.csv")

            if os.path.exists(player_idlist_path) and os.path.exists(cleaned_players_path):
                try:
                    player_idlist_df = pd.read_csv(player_idlist_path)
                    cleaned_players_df = pd.read_csv(cleaned_players_path)

                    merged_df = pd.merge(
                        player_idlist_df[['id', 'first_name', 'second_name']],
                        cleaned_players_df[['first_name', 'second_name', 'element_type']],
                        on=['first_name', 'second_name'],
                        how='inner'
                    )

                    # Rename element_type to position
                    merged_df.rename(columns={'element_type': 'position'}, inplace=True)

                    # Save the DataFrame to a new file
                    merged_df.to_csv(output_file_path, index=False)
                    print(f"Processed and saved: {output_file_path}")
                except Exception as e:
                    print(f"Error processing season {season}: {e}")
            else:
                print(f"Missing required files in {season_path}: player_idlist.csv or cleaned_players.csv")

In [5]:
data_directory = "Fantasy-Premier-League/data"
seasons = ["2024-25", "2023-24", "2022-23", "2021-22", "2020-21"]
process_season_data(data_directory, seasons)

Processed and saved: Fantasy-Premier-League/data/2024-25/processed_players.csv
Processed and saved: Fantasy-Premier-League/data/2023-24/processed_players.csv
Processed and saved: Fantasy-Premier-League/data/2022-23/processed_players.csv
Processed and saved: Fantasy-Premier-League/data/2021-22/processed_players.csv
Processed and saved: Fantasy-Premier-League/data/2020-21/processed_players.csv


In [6]:
def merge_player_ids(data_directory, seasons, output_file="master_player_list.csv"):
    player_data = {}
    next_unique_id = 1
    
    # We want to base ids on 2024-25 season
    main_season = "2024-25"
    main_season_path = os.path.join(data_directory, main_season, "processed_players.csv")
    
    if os.path.exists(main_season_path):
        try:
            main_processed_df = pd.read_csv(main_season_path)
            
            for _, row in main_processed_df.iterrows():
                full_name = f"{row['first_name']} {row['second_name']}"
                if full_name not in player_data:
                    player_data[full_name] = {
                        "First_Name": row['first_name'],
                        "Last_Name": row['second_name'],
                        "Unique_ID": row['id']
                    }
                # Add the 24_id for the main season
                player_data[full_name]['24_id'] = row['id']
                next_unique_id = max(next_unique_id, row['id'] + 1)  # Ensure greater ids to avoid reusing

        except Exception as e:
            print(f"Error processing {main_season_path}: {e}")
    else:
        print(f"Missing processed_players.csv for season: {main_season}")

    # Process other seasons
    for season in seasons:
        
        if season != main_season:
            season_path = os.path.join(data_directory, season, "processed_players.csv")
            if os.path.exists(season_path):
                try:
                    processed_df = pd.read_csv(season_path)
                    
                    season_short = season[:4][-2:]
                    
                    for _, row in processed_df.iterrows():
                        full_name = f"{row['first_name']} {row['second_name']}"
                        if full_name not in player_data:
                            player_data[full_name] = {
                                "First_Name": row['first_name'],
                                "Last_Name": row['second_name'],
                                "Unique_ID": next_unique_id
                            }
                            next_unique_id += 1
                        # Add the season ID
                        player_data[full_name][f"{season_short}_id"] = row['id']
                except Exception as e:
                    print(f"Error processing {season_path}: {e}")

    consolidated_df = pd.DataFrame.from_dict(player_data, orient='index').reset_index(drop=True)
    
    # Ensure all ID columns are integers
    id_columns = [col for col in consolidated_df.columns if col.endswith("_id")]
    consolidated_df[id_columns] = consolidated_df[id_columns].fillna(-1).astype(int)
    
    # Save the consolidated DataFrame to a CSV
    output_path = os.path.join(data_directory, output_file)
    consolidated_df.to_csv(output_path, index=False)
    print(f"Consolidated player data saved to {output_path}")

    return consolidated_df

In [7]:
merge_player_ids(data_directory, seasons)

Consolidated player data saved to Fantasy-Premier-League/data/master_player_list.csv


First_Name             Last_Name  Unique_ID  24_id  23_id  22_id  \
0            Fábio       Ferreira Vieira          1      1      4     25   
1          Gabriel     Fernando de Jesus          2      2      8     28   
2          Gabriel  dos Santos Magalhães          3      3      5     16   
3              Kai               Havertz          4      4      6    145   
4             Karl                  Hein          5      5    646    655   
...            ...                   ...        ...    ...    ...    ...   
1749          Theo              Corbeanu       1750     -1     -1     -1   
1750        Taylor                 Perry       1751     -1     -1     -1   
1751         Lewis              Richards       1752     -1     -1     -1   
1752         Nigel               Lonwijk       1753     -1     -1     -1   
1753  Willian José              Da Silva       1754     -1     -1     -1   

      21_id  20_id  
0        -1     -1  
1       263    282  
2        -1     -1  
3       141    500  
4       532     -1  
...     ...    ...  
1749     -1    610  
1750     -1    611  
1751     -1    615  
1752     -1    629  
1753     -1    642  

[1754 rows x 8 columns]

In [8]:
# Script below was used to get duplicate candidates

# consolidated_file = "master_player_list.csv"
# consolidated_path = os.path.join(data_directory, consolidated_file)
# consolidated_df = pd.read_csv(consolidated_path)

# SIMILARITY_THRESHOLD = 80
# FIRST_NAME_SIMILARITY_THRESHOLD = 40

# def is_pair(player_a, player_b, id_columns):
#     # Check for ID overlaps across seasons
#     id_overlap = any(
#         player_a[col] != -1 and player_b[col] != -1
#         for col in id_columns
#     )
#     if id_overlap:
#         return False
    
#     # Now we check the names similarity
#     first_name_similarity = fuzz.partial_ratio(player_a["First_Name"], player_b["First_Name"])
#     if first_name_similarity <= FIRST_NAME_SIMILARITY_THRESHOLD:
#         return False
    
#     # Check if one last name is contained in the other
#     if player_a["Last_Name"] in player_b["Last_Name"] or player_b["Last_Name"] in player_a["Last_Name"]:
#         return True

#     # Calculate string similarity only if containment check fails
#     similarity = fuzz.partial_ratio(player_a["Last_Name"], player_b["Last_Name"])
#     return similarity >= SIMILARITY_THRESHOLD

# # Identify all ID columns
# id_columns = [col for col in consolidated_df.columns if col.endswith("_id")]
# pairs = []
# for i, player_a in consolidated_df.iterrows():
#     for j, player_b in consolidated_df.iterrows():
#         if i >= j:  # Avoid duplicate and self-pairs
#             continue
#         if is_pair(player_a, player_b, id_columns):
#             pairs.append({
#                 "Player_A_First_Name": player_a["First_Name"],
#                 "Player_A_Last_Name": player_a["Last_Name"],
#                 "Player_B_First_Name": player_b["First_Name"],
#                 "Player_B_Last_Name": player_b["Last_Name"],
#             })

# # Convert pairs to a DataFrame
# created_csv_dir = "created_csv"
# pairs_df = pd.DataFrame(pairs)
# if not pairs_df.empty:
#     output_path = os.path.join(created_csv_dir, "players_with_potential_renames.csv")
#     pairs_df.to_csv(output_path, index=False)
#     print(f"Potential renamed players saved to {output_path}")
# else:
#     print("No potential renamed players found.")

In [9]:
# After manual checking the candidates now we have to update master_player_list.csv 
# (new file will me master_player_verified)
verified_renames = pd.read_csv("created_csv/verified_renames.csv")
master_player_file = "master_player_list.csv"
master_player_path = os.path.join(data_directory, master_player_file)
master_player_list = pd.read_csv(master_player_path)

# Player A ID will be smaller thanks to the way the duplicate finding was implemented
for _, row in verified_renames.iterrows():
    player_a_first = row["Player_A_First_Name"]
    player_a_last = row["Player_A_Last_Name"]
    player_b_first = row["Player_B_First_Name"]
    player_b_last = row["Player_B_Last_Name"]
    
    # Find rows for Player A and Player B in the master_player_list
    player_a_row = master_player_list[
        (master_player_list["First_Name"] == player_a_first) &
        (master_player_list["Last_Name"] == player_a_last)
    ]

    player_b_row = master_player_list[
        (master_player_list["First_Name"] == player_b_first) &
        (master_player_list["Last_Name"] == player_b_last)
    ]

    # Ensure both rows exist
    if player_a_row.empty or player_b_row.empty:
        print(f"Warning: Missing player in master_player_list. Player A: {player_a_first} {player_a_last}, Player B: {player_b_first} {player_b_last}")
        continue

    player_a_id = player_a_row["Unique_ID"].iloc[0]
    player_b_id = player_b_row["Unique_ID"].iloc[0]
    
    # Update the smaller ID row with non-negative season data from the larger ID row
    for season in ["24_id", "23_id", "22_id", "21_id", "20_id"]:
        if player_b_row[season].iloc[0] != -1:
            master_player_list.loc[master_player_list["Unique_ID"] == player_a_id, season] = player_b_row[season].iloc[0]

    # Remove player B
    master_player_list = master_player_list[master_player_list["Unique_ID"] != player_b_id]

# Save the updated master player list to a new file
master_player_list.to_csv("Fantasy-Premier-League/data/master_player_verified.csv", index=False)

In [10]:
def update_processed_players_and_rename_folders(data_directory, seasons, master_player_file):
    master_player_path = os.path.join(data_directory, master_player_file)
    master_player_verified = pd.read_csv(master_player_path)

    for season in seasons:
        season_path = os.path.join(data_directory, season)
        players_folder_path = os.path.join(season_path, "players")
        processed_file = os.path.join(season_path, "processed_players.csv")
        verified_file = os.path.join(season_path, "processed_players_verified.csv")
        
        if season == "2024-25":
            print(f"Processing special case: {season}")

            if os.path.exists(processed_file):
                try:
                    # Simply copy processed_players.csv to processed_players_verified.csv
                    shutil.copy(processed_file, verified_file)
                    print(f"Copied {processed_file} to {verified_file}")
                except Exception as e:
                    print(f"Error copying {processed_file} to {verified_file}: {e}")
            else:
                print(f"Processed players file not found for season: {season}")
            continue

        season_short = season[:4][-2:]  # Extract season short (e.g., "21", "22")
        season_id_column = f"{season_short}_id"

        if os.path.exists(processed_file):
            print(f"Processing season: {season}")
            processed_players = pd.read_csv(processed_file)

            # Get all player folders in the players folder
            player_folders = []
            if os.path.exists(players_folder_path):
                player_folders = [
                    f for f in os.listdir(players_folder_path)
                    if os.path.isdir(os.path.join(players_folder_path, f))
                ]

            # Update IDs and rename folders
            for index, row in processed_players.iterrows():
                current_id = row["id"]
                # Match the season-specific ID in master_player_verified
                matching_row = master_player_verified[master_player_verified[season_id_column] == current_id]

                if not matching_row.empty:
                    new_data = matching_row.iloc[0]
                    new_unique_id = new_data["Unique_ID"]
                    new_first_name = new_data["First_Name"]
                    new_last_name = new_data["Last_Name"]

                    # Update the processed_players row
                    processed_players.at[index, "id"] = new_unique_id
                    processed_players.at[index, "first_name"] = new_first_name
                    processed_players.at[index, "second_name"] = new_last_name

                    # Find and rename the player's folder
                    matching_folder = next(
                        (f for f in player_folders if f.endswith(f"_{current_id}")), None
                    )
                    if matching_folder:
                        old_path = os.path.join(players_folder_path, matching_folder)
                        new_folder_name = f"{new_first_name}_{new_last_name}_{new_unique_id}"
                        new_path = os.path.join(players_folder_path, new_folder_name)

                        # Ensure destination directory does not already exist
                        if os.path.exists(new_path):
                            continue
                        try:
                            shutil.move(old_path, new_path)
                            print(f"Successfully renamed folder {matching_folder} to {new_folder_name}")
                            player_folders.remove(matching_folder)
                        except Exception as e:
                            print(f"Error moving {old_path} to {new_path}: {e}")

            # Save the updated processed_players file
            processed_players.to_csv(verified_file, index=False)
            print(f"Updated file and folders saved for season: {season}")
        else:
            print(f"Processed players file not found for season: {season}")

In [11]:
master_player_file = "master_player_verified.csv"

update_processed_players_and_rename_folders(data_directory, seasons, master_player_file)

Processing special case: 2024-25
Copied Fantasy-Premier-League/data/2024-25/processed_players.csv to Fantasy-Premier-League/data/2024-25/processed_players_verified.csv
Processing season: 2023-24
Successfully renamed folder Folarin_Balogun_1 to Folarin_Balogun_679
Successfully renamed folder Cédric_Alves Soares_2 to Cédric_Alves Soares_680
Successfully renamed folder Mohamed_Elneny_3 to Mohamed_Elneny_681
Successfully renamed folder Fábio_Ferreira Vieira_4 to Fábio_Ferreira Vieira_1
Successfully renamed folder Gabriel_dos Santos Magalhães_5 to Gabriel_dos Santos Magalhães_3
Successfully renamed folder Kai_Havertz_6 to Kai_Havertz_4
Successfully renamed folder Gabriel_Fernando de Jesus_8 to Gabriel_Fernando de Jesus_2
Successfully renamed folder Jorge Luiz_Frello Filho_9 to Jorge Luiz_Frello Filho_7
Successfully renamed folder Jakub_Kiwior_10 to Jakub_Kiwior_8
Successfully renamed folder Marcus_Oliveira Alencar_11 to Marcus_Oliveira Alencar_682
Successfully renamed folder Gabriel_Martine

Successfully renamed folder Santiago_Bueno_697 to Santiago_Bueno_564
Successfully renamed folder Enso_González_698 to Enso_González_547
Successfully renamed folder Nathan_Fraser_704 to Nathan_Fraser_546
Successfully renamed folder Jean-Ricner_Bellegarde_715 to Jean-Ricner_Bellegarde_535
Successfully renamed folder Matthew_Whittingham_749 to Matthew_Whittingham_1058
Successfully renamed folder Tawanda_Chirewa_750 to Tawanda_Chirewa_538
Successfully renamed folder Justin_Hubner_751 to Justin_Hubner_1059
Successfully renamed folder Owen_Hesketh_769 to Owen_Hesketh_1060
Successfully renamed folder Ty_Barnett_770 to Ty_Barnett_1061
Successfully renamed folder Harvey_Griffiths_787 to Harvey_Griffiths_1062
Successfully renamed folder Yerson_Mosquera_788 to Yerson_Mosquera_558
Successfully renamed folder Noha_Lemina_800 to Noha_Lemina_1063
Successfully renamed folder Wesley_Okoduwa_832 to Wesley_Okoduwa_1064
Successfully renamed folder Leon_Chiwome_836 to Leon_Chiwome_539
Successfully renamed 

Successfully renamed folder Dennis_Praet_549 to Dennis_Praet_1154
Successfully renamed folder Alex_Smithies_581 to Alex_Smithies_1155
Successfully renamed folder Wout_Faes_612 to Wout_Faes_291
Successfully renamed folder Sammy_Braybrooke_639 to Sammy_Braybrooke_1156
Successfully renamed folder Joe_Wormleighton_645 to Joe_Wormleighton_1157
Successfully renamed folder Kasey_McAteer_687 to Kasey_McAteer_299
Successfully renamed folder Victor_Kristiansen_709 to Victor_Kristiansen_296
Successfully renamed folder Mateus_Cardoso Lemos Martins_715 to Mateus_Cardoso Lemos Martins_1158
Successfully renamed folder Harry_Souttar_727 to Harry_Souttar_303
Successfully renamed folder Wanya_Marçal-Madivadua_735 to Wanya_Marçal-Madivádua_297
Successfully renamed folder Liam_Cooper_221 to Liam_Cooper_1160
Successfully renamed folder Luke_Ayling_222 to Luke_Ayling_1161
Successfully renamed folder Mateusz_Klich_223 to Mateusz_Klich_1162
Successfully renamed folder Adam_Forshaw_224 to Adam_Forshaw_1163
Suc

Successfully renamed folder Takehiro_Tomiyasu_590 to Takehiro_Tomiyasu_681
Successfully renamed folder Charlie_Patino_664 to Charlie_Patino_1294
Successfully renamed folder Omari_Hutchinson_692 to Omari_Giraud-Hutchinson_274
Successfully renamed folder Salah-Eddine_Oulad M'hand_693 to Salah-Eddine_Oulad M'hand_638
Successfully renamed folder Mika_Biereth_694 to Mika_Biereth_1295
Successfully renamed folder Ryan_Alebiosu_695 to Ryan_Alebiosu_1296
Successfully renamed folder Zach_Awe_705 to Zach_Awe_1297
Successfully renamed folder Zak_Swanson_711 to Zak_Swanson_1298
Successfully renamed folder Mazeed_Ogungbo_719 to Mazeed_Ogungbo_1299
Successfully renamed folder Marcelo_Flores_720 to Marcelo_Flores_1300
Successfully renamed folder Miguel_Azeez_721 to Miguel_Azeez_1301
Successfully renamed folder Alex_Kirk_730 to Alex_Kirk_1302
Successfully renamed folder Calum_Chambers_10 to Calum_Chambers_689
Successfully renamed folder Jed_Steer_28 to Jed_Steer_1303
Successfully renamed folder Conor_H

Successfully renamed folder Anthony_Martial_278 to Anthony_Martial_931
Successfully renamed folder Alex Nicolao_Telles_279 to Alex_Telles_927
Successfully renamed folder Dean_Henderson_280 to Dean_Henderson_201
Successfully renamed folder Marcus_Rashford_281 to Marcus_Rashford_385
Successfully renamed folder Axel_Tuanzebe_283 to Axel_Tuanzebe_282
Successfully renamed folder Victor_Lindelöf_284 to Victor_Lindelöf_376
Successfully renamed folder Scott_McTominay_285 to Scott_McTominay_381
Successfully renamed folder Eric_Bailly_286 to Eric_Bailly_929
Successfully renamed folder Aaron_Wan-Bissaka_288 to Aaron_Wan-Bissaka_388
Successfully renamed folder Mason_Greenwood_289 to Mason_Greenwood_1414
Successfully renamed folder Juan_Mata_459 to Juan_Mata_1415
Successfully renamed folder Jadon_Sancho_485 to Jadon_Sancho_386
Successfully renamed folder Tom_Heaton_509 to Tom_Heaton_374
Successfully renamed folder José Diogo_Dalot Teixeira_510 to Diogo_Dalot Teixeira_369
Successfully renamed folder

Successfully renamed folder Nick_Pope_96 to Nick_Pope_413
Successfully renamed folder Charlie_Taylor_97 to Charlie_Taylor_475
Successfully renamed folder Josh_Brownhill_98 to Josh_Brownhill_757
Successfully renamed folder Bailey_Peacock-Farrell_99 to Bailey_Peacock-Farrell_769
Successfully renamed folder Dwight_McNeil_100 to Dwight_McNeil_230
Successfully renamed folder Jimmy_Dunne_519 to Jimmy_Dunne_1577
Successfully renamed folder Bobby_Thomas_520 to Bobby_Thomas_772
Successfully renamed folder Josh_Benson_535 to Josh_Benson_1347
Successfully renamed folder Anthony_Driscoll-Glennon_536 to Anthony_Driscoll-Glennon_1578
Successfully renamed folder Mace_Goodridge_551 to Mace_Goodridge_1579
Successfully renamed folder Will_Norris_583 to Will_Norris_1346
Successfully renamed folder Max_Thompson_591 to Max_Thompson_1580
Successfully renamed folder Lewis_Richardson_592 to Lewis_Richardson_1348
Successfully renamed folder Anthony_Mancini_612 to Anthony_Mancini_1352
Successfully renamed folde

Successfully renamed folder Nathan_Tella_524 to Nathan_Tella_1237
Successfully renamed folder Ibrahima_Diallo_565 to Ibrahima_Diallo_1240
Successfully renamed folder Daniel_N'Lundulu_590 to Daniel_N'Lundulu_1459
Successfully renamed folder Kayne_Ramsay_598 to Kayne_Ramsay_1685
Successfully renamed folder Kgaogelo_Chauke_624 to Kgaogelo_Chauke_1466
Successfully renamed folder Harry_Lewis_625 to Harry_Lewis_1463
Successfully renamed folder Will_Ferry_634 to Will_Ferry_1686
Successfully renamed folder Allan_Tchaptchet_635 to Allan_Tchaptchet_1687
Successfully renamed folder Caleb_Watts_636 to Caleb_Watts_1688
Successfully renamed folder Alexandre_Jankewitz_643 to Alexandre_Jankewitz_1689
Successfully renamed folder Ryan_Finnigan_655 to Ryan_Finnigan_1248
Successfully renamed folder Hugo_Lloris_383 to Hugo_Lloris_1029
Successfully renamed folder Danny_Rose_384 to Danny_Rose_1480
Successfully renamed folder Moussa_Sissoko_385 to Moussa_Sissoko_1478
Successfully renamed folder Toby_Alderweir

In [12]:
# Now we will start manipulating player's data. First let's add to each player row his position
# (1 - GK, 2 - DEF, 3 - MID, 4 - FWD) and add it to the folder's name as well
# Let's also add the Full Name of the player


def update_player_folders_and_gw_data(season_path):
    position_mapping = {"GK": 1, "DEF": 2, "MID": 3, "FWD": 4}
    
    processed_players_path = os.path.join(season_path, "processed_players_verified.csv")
    players_folder_path = os.path.join(season_path, "players")
    
    if not os.path.exists(processed_players_path):
        print(f"{processed_players_path} not found.")
        return
    
    processed_players = pd.read_csv(processed_players_path)
    
    for _, row in processed_players.iterrows():
        player_id = row['id']
        first_name = row['first_name']
        second_name = row['second_name']
        position_str = row['position']
        
        pos_numeric = position_mapping.get(position_str, 0)  # Default to 0 if unknown
        if pos_numeric == 0:
            print(f"Unknown position for player {first_name} {second_name} (ID: {player_id}). Skipping.")
            continue
        
        old_folder_name = f"{first_name}_{second_name}_{player_id}"
        old_folder_path = os.path.join(players_folder_path, old_folder_name)
        if not os.path.exists(old_folder_path):
            print(f"Folder {old_folder_name} not found. Skipping.")
            continue

        new_folder_name = f"{position_str}_{old_folder_name}"
        new_folder_path = os.path.join(players_folder_path, new_folder_name)
        
        try:
            shutil.move(old_folder_path, new_folder_path)
            print(f"Renamed folder: {old_folder_name} -> {new_folder_name}")
        except Exception as e:
            print(f"Error renaming {old_folder_name} to {new_folder_name}: {e}")
            continue
        
        gw_file_path = os.path.join(new_folder_path, "gw.csv")
        
        if os.path.exists(gw_file_path):
            try:
                gw_data = pd.read_csv(gw_file_path)
                
                # Update element to unique_id and rename column
                if 'element' in gw_data.columns:
                    gw_data.rename(columns={'element': 'unique_id'}, inplace=True)
                    gw_data['unique_id'] = player_id
                
                # Add POS and Full Name
                gw_data['POS'] = pos_numeric
                gw_data['Full Name'] = f"{first_name} {second_name}"
                
                # Save updated gw.csv
                gw_data.to_csv(gw_file_path, index=False)
                print(f"Updated POS and unique_id in {gw_file_path}")
            except Exception as e:
                print(f"Error updating {gw_file_path}: {e}")

In [13]:
season_paths = [
    "Fantasy-Premier-League/data/2020-21",
    "Fantasy-Premier-League/data/2021-22",
    "Fantasy-Premier-League/data/2022-23",
    "Fantasy-Premier-League/data/2023-24",
    "Fantasy-Premier-League/data/2024-25"
]

for season_path in season_paths:
    print(f"Processing season: {season_path}")
    update_player_folders_and_gw_data(season_path)

Processing season: Fantasy-Premier-League/data/2020-21
Renamed folder: Mesut_Özil_1553 -> MID_Mesut_Özil_1553
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Mesut_Özil_1553/gw.csv
Renamed folder: Sokratis_Papastathopoulos_1554 -> DEF_Sokratis_Papastathopoulos_1554
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_Sokratis_Papastathopoulos_1554/gw.csv
Renamed folder: David_Luiz Moreira Marinho_1555 -> DEF_David_Luiz Moreira Marinho_1555
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_David_Luiz Moreira Marinho_1555/gw.csv
Renamed folder: Pierre-Emerick_Aubameyang_795 -> MID_Pierre-Emerick_Aubameyang_795
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Pierre-Emerick_Aubameyang_795/gw.csv
Renamed folder: Cédric_Alves Soares_680 -> DEF_Cédric_Alves Soares_680
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_Cédric_Alves Soares_680/gw.csv
Renamed fol

Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/GK_Kepa_Arrizabalaga_152/gw.csv
Renamed folder: N'Golo_Kanté_1101 -> MID_N'Golo_Kanté_1101
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_N'Golo_Kanté_1101/gw.csv
Renamed folder: Hakim_Ziyech_797 -> MID_Hakim_Ziyech_797
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Hakim_Ziyech_797/gw.csv
Renamed folder: Andreas_Christensen_1356 -> DEF_Andreas_Christensen_1356
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_Andreas_Christensen_1356/gw.csv
Renamed folder: Timo_Werner_509 -> FWD_Timo_Werner_509
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/FWD_Timo_Werner_509/gw.csv
Renamed folder: Tammy_Abraham_1358 -> FWD_Tammy_Abraham_1358
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/FWD_Tammy_Abraham_1358/gw.csv
Renamed folder: Christian_Pulisic_794 -> MID_Christian_Pulisic_794
Updated 

Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_Niels_Nkounkou_1124/gw.csv
Renamed folder: Ben_Godfrey_830 -> DEF_Ben_Godfrey_830
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_Ben_Godfrey_830/gw.csv
Renamed folder: Robin_Olsen_51 -> GK_Robin_Olsen_51
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/GK_Robin_Olsen_51/gw.csv
Renamed folder: Ellis_Simms_832 -> FWD_Ellis_Simms_832
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/FWD_Ellis_Simms_832/gw.csv
Renamed folder: Tyler_Onyango_836 -> MID_Tyler_Onyango_836
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Tyler_Onyango_836/gw.csv
Renamed folder: Joshua_King_854 -> FWD_Joshua_King_854
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/FWD_Joshua_King_854/gw.csv
Renamed folder: Kyle_John_1129 -> DEF_Kyle_John_1129
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/pl

Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Thakgalo_Leshabela_1624/gw.csv
Renamed folder: Sidnei_Tavares_1625 -> MID_Sidnei_Tavares_1625
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Sidnei_Tavares_1625/gw.csv
Renamed folder: Shane_Flynn_1626 -> MID_Shane_Flynn_1626
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Shane_Flynn_1626/gw.csv
Renamed folder: Thanawat_Suengchitthawon_1627 -> MID_Thanawat_Suengchitthawon_1627
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Thanawat_Suengchitthawon_1627/gw.csv
Renamed folder: Tawanda_Maswanhise_1628 -> MID_Tawanda_Maswanhise_1628
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Tawanda_Maswanhise_1628/gw.csv
Renamed folder: Pablo_Hernández Domínguez_1381 -> MID_Pablo_Hernández Domínguez_1381
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Pablo_Hernández Domínguez_138

Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_Kyle_Walker_363/gw.csv
Renamed folder: Ilkay_Gündogan_625 -> MID_Ilkay_Gündogan_625
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Ilkay_Gündogan_625/gw.csv
Renamed folder: Kevin_De Bruyne_345 -> MID_Kevin_De Bruyne_345
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Kevin_De Bruyne_345/gw.csv
Renamed folder: John_Stones_362 -> DEF_John_Stones_362
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_John_Stones_362/gw.csv
Renamed folder: Benjamin_Mendy_1397 -> DEF_Benjamin_Mendy_1397
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/DEF_Benjamin_Mendy_1397/gw.csv
Renamed folder: Riyad_Mahrez_920 -> MID_Riyad_Mahrez_920
Updated POS and unique_id in Fantasy-Premier-League/data/2020-21/players/MID_Riyad_Mahrez_920/gw.csv
Renamed folder: Raheem_Sterling_186 -> MID_Raheem_Sterling_186
Updated POS and unique_id 

...

Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Sander_Berge_622/gw.csv
Renamed folder: Ali_Al-Hamadi_260 -> FWD_Ali_Al-Hamadi_260
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/FWD_Ali_Al-Hamadi_260/gw.csv
Renamed folder: Elkan_Baggott_261 -> DEF_Elkan_Baggott_261
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/DEF_Elkan_Baggott_261/gw.csv
Renamed folder: Nathan_Broadhead_262 -> MID_Nathan_Broadhead_262
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Nathan_Broadhead_262/gw.csv
Renamed folder: Cameron_Burgess_263 -> DEF_Cameron_Burgess_263
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/DEF_Cameron_Burgess_263/gw.csv
Renamed folder: Wes_Burns_264 -> MID_Wes_Burns_264
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Wes_Burns_264/gw.csv
Renamed folder: Conor_Chaplin_265 -> MID_Conor_Chaplin_265
Updated POS and unique_id in Fan

Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/DEF_Ibrahima_Konaté_326/gw.csv
Renamed folder: Luis_Díaz_327 -> MID_Luis_Díaz_327
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Luis_Díaz_327/gw.csv
Renamed folder: Mohamed_Salah_328 -> MID_Mohamed_Salah_328
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Mohamed_Salah_328/gw.csv
Renamed folder: Alexis_Mac Allister_329 -> MID_Alexis_Mac Allister_329
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Alexis_Mac Allister_329/gw.csv
Renamed folder: James_McConnell_330 -> MID_James_McConnell_330
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_James_McConnell_330/gw.csv
Renamed folder: Tyler_Morton_331 -> MID_Tyler_Morton_331
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Tyler_Morton_331/gw.csv
Renamed folder: Nathaniel_Phillips_332 -> DEF_Nathaniel_Phillips_332
Updated POS a

Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/GK_Martin_Dúbravka_396/gw.csv
Renamed folder: Anthony_Gordon_398 -> MID_Anthony_Gordon_398
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Anthony_Gordon_398/gw.csv
Renamed folder: Lewis_Hall_399 -> DEF_Lewis_Hall_399
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/DEF_Lewis_Hall_399/gw.csv
Renamed folder: Isaac_Hayden_400 -> MID_Isaac_Hayden_400
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Isaac_Hayden_400/gw.csv
Renamed folder: Alexander_Isak_401 -> FWD_Alexander_Isak_401
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/FWD_Alexander_Isak_401/gw.csv
Renamed folder: Jacob_Murphy_402 -> MID_Jacob_Murphy_402
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Jacob_Murphy_402/gw.csv
Renamed folder: Joelinton Cássio_Apolinário de Lira_403 -> MID_Joelinton Cássio_Apolinário de Lira_40

Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/FWD_Sékou_Mara_468/gw.csv
Renamed folder: Alex_McCarthy_469 -> GK_Alex_McCarthy_469
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/GK_Alex_McCarthy_469/gw.csv
Renamed folder: Paul_Onuachu_470 -> FWD_Paul_Onuachu_470
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/FWD_Paul_Onuachu_470/gw.csv
Renamed folder: Will_Smallbone_471 -> MID_Will_Smallbone_471
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Will_Smallbone_471/gw.csv
Renamed folder: Jack_Stephens_472 -> DEF_Jack_Stephens_472
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/DEF_Jack_Stephens_472/gw.csv
Renamed folder: Ross_Stewart_473 -> FWD_Ross_Stewart_473
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/FWD_Ross_Stewart_473/gw.csv
Renamed folder: Sugawara_Yukinari_474 -> DEF_Sugawara_Yukinari_474
Updated POS and unique_id in Fanta

Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/GK_Daniel_Bentley_536/gw.csv
Renamed folder: Francisco Jorge_Tomás Oliveira_537 -> MID_Francisco Jorge_Tomás Oliveira_537
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Francisco Jorge_Tomás Oliveira_537/gw.csv
Renamed folder: Tawanda_Chirewa_538 -> MID_Tawanda_Chirewa_538
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Tawanda_Chirewa_538/gw.csv
Renamed folder: Leon_Chiwome_539 -> FWD_Leon_Chiwome_539
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/FWD_Leon_Chiwome_539/gw.csv
Renamed folder: Luke_Cundle_540 -> MID_Luke_Cundle_540
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/MID_Luke_Cundle_540/gw.csv
Renamed folder: Matheus_Santos Carneiro Da Cunha_541 -> FWD_Matheus_Santos Carneiro Da Cunha_541
Updated POS and unique_id in Fantasy-Premier-League/data/2024-25/players/FWD_Matheus_Santos Carneiro Da Cunha

In [14]:
# Player data doesn't have his own team id (and they can switch teams during season so we have to add that)
# Let's also rename round to gameweek
def add_own_team_to_players(data_directory, season, fixtures_file):
    """
    Adds the 'own_team' column to gw.csv files for each player and renames 'round' to 'gameweek'.

    Args:
        data_directory (str): Base directory containing the season data.
        season (str): Season name (e.g., "2022-23").
        fixtures_file (str): Name of the fixtures file (e.g., "fixtures.csv").

    Returns:
        None
    """
    fixtures_path = os.path.join(data_directory, season, fixtures_file)
    if not os.path.exists(fixtures_path):
        print(f"Fixtures file not found for season {season}. Skipping.")
        return
    
    fixtures = pd.read_csv(fixtures_path)
    players_folder = os.path.join(data_directory, season, "players")
    
    if not os.path.exists(players_folder):
        print(f"Players folder not found for season {season}. Skipping.")
        return
    
    for player_folder in os.listdir(players_folder):
        player_folder_path = os.path.join(players_folder, player_folder)
        if os.path.isdir(player_folder_path):
            gw_file_path = os.path.join(player_folder_path, "gw.csv")
            
            if os.path.exists(gw_file_path):
                try:
                    gw_data = pd.read_csv(gw_file_path)

                    # Merge fixtures data to get team_a and team_h
                    gw_data = gw_data.merge(
                        fixtures[['id', 'team_a', 'team_h']],
                        left_on='fixture',
                        right_on='id',
                        how='left'
                    )

                    # Determine own_team based on was_home
                    gw_data['own_team'] = gw_data.apply(
                        lambda x: x['team_h'] if x['was_home'] else x['team_a'], axis=1
                    )
                    
                    # Rename 'round' to 'gameweek'
                    if 'round' in gw_data.columns:
                        gw_data.rename(columns={'round': 'gameweek'}, inplace=True)

                    # Drop unnecessary columns (like the merged fixture id)
                    gw_data.drop(columns=['id', 'team_a', 'team_h'], inplace=True)

                    # Save the updated gw.csv
                    gw_data.to_csv(gw_file_path, index=False)
                    print(f"Updated {gw_file_path} with own_team and gameweek.")
                except Exception as e:
                    print(f"Error processing {gw_file_path}: {e}")

# Example usage
data_directory = "Fantasy-Premier-League/data"
seasons = ["2020-21", "2021-22", "2022-23", "2023-24", "2024-25"]
fixtures_file = "fixtures.csv"

for season in seasons:
    print(f"Processing season: {season}")
    add_own_team_to_players(data_directory, season, fixtures_file)

Processing season: 2020-21
Updated Fantasy-Premier-League/data/2020-21/players/GK_Mathew_Ryan_1329/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Marcos_Rojo_1657/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Frederico_Rodrigues de Paula Santos_934/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Raúl_Jiménez_252/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Joe_Rodon_1036/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Martin_Ødegaard_13/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Patrick_Bamford_1170/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Mattéo_Guendouzi_1293/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Florian_Lejeune_1663/g

Updated Fantasy-Premier-League/data/2020-21/players/MID_Bruno_Cavaco Jordão_1055/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Joel_Matip_859/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Benjamin_Mendy_1397/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Wilfred_Ndidi_300/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Florian_Lejeune_1660/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Jake_Cain_1641/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Michael_Verrips_1676/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Aaron_Wan-Bissaka_388/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Paul_Dummett_955/gw.csv with own_team and gameweek.
Updated 

Updated Fantasy-Premier-League/data/2020-21/players/MID_Hamza_Choudhury_287/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Leandro_Trossard_23/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Lucas_Rodrigues Moura da Silva_1254/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Daniel_Langley_1666/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Mbwana Ally_Samatta_1310/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Lewis_Dunk_120/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/GK_João_Neves Virgínia_227/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Declan_Rice_16/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Yoshinori_Muto_1664/gw.csv with own_team an

Updated Fantasy-Premier-League/data/2020-21/players/FWD_Roberto_Firmino_1195/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Ben_Osborn_1005/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Sergio_Romero_1651/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Jordan_Stevens_1633/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Scott_Carson_344/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Kamil_Grosicki_1702/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Alexandre_Lacazette_1282/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Aaron_Mooy_1565/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Max_Lowe_1001/gw.csv with own_team and gameweek.
Updated Fantasy

Updated Fantasy-Premier-League/data/2020-21/players/GK_Kamil_Miazek_1632/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Gary_Cahill_1588/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Fabian_Delph_1366/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Yan_Valery_1239/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Glenn_Murray_1564/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Josh_Sims_1683/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Alex_Telles_927/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Sébastien_Haller_1733/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Indiana_Vassilev_1563/gw.csv with own_team and gameweek.
Updated Fantasy-Prem

...

Updated Fantasy-Premier-League/data/2024-25/players/MID_Georginio_Rutter_618/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Luke_Shaw_387/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Joe_Willock_420/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/FWD_Deniz_Undav_143/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Levi_Colwill_162/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Facundo_Buonanotte_117/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Wesley_Fofana_189/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/FWD_Michail_Antonio_512/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Phil_Foden_348/gw.csv with own_team and gameweek.
Updated Fantasy-Premi

Updated Fantasy-Premier-League/data/2024-25/players/DEF_Kevin_Mbabu_250/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/FWD_Eddie_Nketiah_11/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Dango_Ouattara_74/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Pedro_Cardoso de Lima_561/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_James_Tarkowski_236/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Pierre-Emile_Højbjerg_490/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Alex_Mighten_435/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Dean_Huijsen_580/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Lewis_Dobbin_37/gw.csv with own_team and gameweek.
Updated 

Updated Fantasy-Premier-League/data/2024-25/players/DEF_Jannik_Vestergaard_307/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Rúben_Gato Alves Dias_361/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Christian_Nørgaard_101/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Ângelo Gabriel_Borges Damaceno_151/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Luis_Díaz_327/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Jurriën_Timber_6/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/FWD_Ross_Stewart_473/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Pascal_Groß_125/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Amadou_Onana_233/gw.csv with own_team and gam

Updated Fantasy-Premier-League/data/2024-25/players/DEF_Valentín_Barco_116/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Neco_Williams_437/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/GK_Harvey_Davies_669/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Hannibal_Mejbri_373/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/GK_Daniel_Bentley_536/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Jaidon_Anthony_61/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Odeluga_Offiah_139/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Rodrigo_Bentancur_480/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Raheem_Sterling_186/gw.csv with own_team and gameweek.
Updated Fa

Updated Fantasy-Premier-League/data/2024-25/players/DEF_Jahmai_Simpson-Pusey_672/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Tariq_Lamptey_131/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Moussa_Diaby_34/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Sander_Berge_622/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Kenny_Tete_257/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Amad_Diallo_364/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/GK_Daniel_Iversen_294/gw.csv with own_team and gameweek.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Daniel_Muñoz_211/gw.csv with own_team and gameweek.


In [15]:
# Now we can add short team names for player and opponent and also strengths of both teams from teams.csv
def add_team_strengths_and_short_names(data_directory, season, teams_file):
    teams_path = os.path.join(data_directory, season, teams_file)
    
    if not os.path.exists(teams_path):
        print(f"Teams file not found for season {season}. Skipping.")
        return
    
    teams_data = pd.read_csv(teams_path).set_index('id')

    players_folder = os.path.join(data_directory, season, "players")
    if not os.path.exists(players_folder):
        print(f"Players folder not found for season {season}. Skipping.")
        return

    for player_folder in os.listdir(players_folder):
        player_folder_path = os.path.join(players_folder, player_folder)
        gw_file_path = os.path.join(player_folder_path, "gw.csv")
        
        if os.path.exists(gw_file_path):
            try:
                gw_data = pd.read_csv(gw_file_path)

                # Merge opponent team strengths and short name
                gw_data = gw_data.merge(
                    teams_data[['short_name', 'strength_attack_home', 'strength_attack_away', 
                                'strength_defence_home', 'strength_defence_away']],
                    left_on='opponent_team',
                    right_index=True,
                    how='left'
                ).rename(columns={
                    'short_name': 'opponent_short_name',
                    'strength_attack_home': 'opponent_attack_home',
                    'strength_attack_away': 'opponent_attack_away',
                    'strength_defence_home': 'opponent_defence_home',
                    'strength_defence_away': 'opponent_defence_away'
                })

                # Add opponent strengths based on was_home
                gw_data['opponent_attack'] = gw_data.apply(
                    lambda x: x['opponent_attack_away'] if x['was_home'] else x['opponent_attack_home'], axis=1
                )
                gw_data['opponent_defense'] = gw_data.apply(
                    lambda x: x['opponent_defence_away'] if x['was_home'] else x['opponent_defence_home'], axis=1
                )

                # Merge own team strengths and short name
                gw_data = gw_data.merge(
                    teams_data[['short_name', 'strength_attack_home', 'strength_attack_away', 
                                'strength_defence_home', 'strength_defence_away']],
                    left_on='own_team',
                    right_index=True,
                    how='left'
                ).rename(columns={
                    'short_name': 'own_short_name',
                    'strength_attack_home': 'own_attack_home',
                    'strength_attack_away': 'own_attack_away',
                    'strength_defence_home': 'own_defence_home',
                    'strength_defence_away': 'own_defence_away'
                })

                # Add own team strengths based on was_home
                gw_data['own_attack'] = gw_data.apply(
                    lambda x: x['own_attack_home'] if x['was_home'] else x['own_attack_away'], axis=1
                )
                gw_data['own_defense'] = gw_data.apply(
                    lambda x: x['own_defence_home'] if x['was_home'] else x['own_defence_away'], axis=1
                )

                # Drop temporary columns to keep only relevant data
                gw_data.drop(columns=[
                    'opponent_attack_home', 'opponent_attack_away',
                    'opponent_defence_home', 'opponent_defence_away',
                    'own_attack_home', 'own_attack_away',
                    'own_defence_home', 'own_defence_away'
                ], inplace=True)

                # Save the updated gw.csv
                gw_data.to_csv(gw_file_path, index=False)
                print(f"Updated {gw_file_path} with team strengths and short names.")
            except Exception as e:
                print(f"Error processing {gw_file_path}: {e}")

data_directory = "Fantasy-Premier-League/data"
seasons = ["2020-21", "2021-22", "2022-23", "2023-24", "2024-25"]
teams_file = "teams.csv"

for season in seasons:
    print(f"Processing season: {season}")
    add_team_strengths_and_short_names(data_directory, season, teams_file)

Processing season: 2020-21
Updated Fantasy-Premier-League/data/2020-21/players/GK_Mathew_Ryan_1329/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Marcos_Rojo_1657/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Frederico_Rodrigues de Paula Santos_934/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Raúl_Jiménez_252/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Joe_Rodon_1036/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Martin_Ødegaard_13/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Patrick_Bamford_1170/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Mattéo_Guendouzi_1293/gw.csv with team strengths and short names.
Update

Updated Fantasy-Premier-League/data/2020-21/players/DEF_Kyle_Bartley_1704/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Facundo_Pellistri Rebollo_384/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Joe_Rodon_1032/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_André-Frank_Zambo Anguissa_1611/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_John_Egan_999/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Allan_Tchaptchet_1687/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Nigel_Lonwijk_1750/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Tyrick_Mitchell_210/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League

Updated Fantasy-Premier-League/data/2020-21/players/MID_Marcus_Rashford_385/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Ben_Davies_484/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_James_McCarthy_1590/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Reece_James_172/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Willy_Caballero_1244/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Ederson_Santana de Moraes_347/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Anwar_El Ghazi_1071/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Ciaran_Clark_1215/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-2

Updated Fantasy-Premier-League/data/2020-21/players/MID_Carney_Chukwuemeka_161/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Wilfried_Zaha_1113/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_George_Baldock_993/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Liam_Hughes_1642/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Robert_Snodgrass_1715/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Jonjoe_Kenny_1373/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Jean-Philippe_Mateta_207/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Nicolas_Pépé_679/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-

Updated Fantasy-Premier-League/data/2020-21/players/MID_Mario_Lemina_557/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Ben_Mee_100/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Rekeem_Harper_1714/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Aaron_Connolly_739/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Sam_Greenwood_1174/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Teden_Mengi_900/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Matheus_Pereira_1717/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Mark_Gillespie_948/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Edd

...

Updated Fantasy-Premier-League/data/2024-25/players/MID_Ibrahim_Sangaré_442/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Jack_Hinshelwood_126/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Tyrone_Mings_49/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_David_Ozoh_212/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Ryan_Fraser_397/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Pablo_Sarabia_565/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Abdul_Fatawu_570/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Imari_Samuels_663/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Fly

Updated Fantasy-Premier-League/data/2024-25/players/DEF_Malo_Gusto_171/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/GK_Tom_Heaton_374/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Bruno_Borges Fernandes_366/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Abdoulaye_Doucouré_217/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Andreas_Hoelgebaum Pereira_240/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Sergio_Reguilón_496/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/GK_José_Malheiro de Sá_554/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Lewis_O'Brien_439/gw.csv with team strengths and short names.
Updated Fantasy-Premier-Leagu

Updated Fantasy-Premier-League/data/2024-25/players/MID_Pascal_Groß_125/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Amadou_Onana_233/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Brajan_Gruda_595/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Will_Smallbone_471/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/FWD_Raúl_Jiménez_252/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Adam_Webster_147/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Caleb_Wiley_575/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/FWD_Sékou_Mara_468/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Ilkay_Günd

Updated Fantasy-Premier-League/data/2024-25/players/MID_Tom_Cairney_243/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Harry_Wilson_259/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Tyler_Morton_331/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Sil_Swinkels_640/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Jordan_Ayew_192/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Valentín_Barco_116/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Neco_Williams_437/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/GK_Harvey_Davies_669/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Hanniba

Updated Fantasy-Premier-League/data/2024-25/players/GK_Asmir_Begovic_624/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Rico_Henry_92/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Manuel_Ugarte_652/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Diogo_Teixeira da Silva_317/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Malang_Sarr_176/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/DEF_Rayan_Aït-Nouri_533/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/MID_Reiss_Nelson_10/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/GK_Alfie_Whiteman_510/gw.csv with team strengths and short names.
Updated Fantasy-Premier-League/data/2024-25/players/D

In [16]:
# We also can take into consideration whether there were fans at the stadium (during covid the 
# home team advantage wasn't so strong)
def add_crowds_to_gw(data_directory, season):
    no_crowds_start = datetime(2020, 3, 15, tzinfo=timezone.utc)
    no_crowds_end = datetime(2021, 6, 17, tzinfo=timezone.utc)

    players_folder = os.path.join(data_directory, season, "players")
    if not os.path.exists(players_folder):
        print(f"Players folder not found for season {season}. Skipping.")
        return
    
    for player_folder in os.listdir(players_folder):
        player_folder_path = os.path.join(players_folder, player_folder)
        gw_file_path = os.path.join(player_folder_path, "gw.csv")
        
        if os.path.exists(gw_file_path):
            try:
                gw_data = pd.read_csv(gw_file_path)

                gw_data['kickoff_time'] = pd.to_datetime(gw_data['kickoff_time']).dt.tz_convert('UTC')

                gw_data['crowds'] = gw_data['kickoff_time'].apply(
                    lambda x: 0 if no_crowds_start <= x <= no_crowds_end else 1
                )

                gw_data.to_csv(gw_file_path, index=False)
                print(f"Updated {gw_file_path} with crowds column.")
            except Exception as e:
                print(f"Error processing {gw_file_path}: {e}")

data_directory = "Fantasy-Premier-League/data"
seasons = ["2020-21", "2021-22", "2022-23", "2023-24", "2024-25"]

for season in seasons:
    print(f"Processing season: {season}")
    add_crowds_to_gw(data_directory, season)

Processing season: 2020-21
Updated Fantasy-Premier-League/data/2020-21/players/GK_Mathew_Ryan_1329/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Marcos_Rojo_1657/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Frederico_Rodrigues de Paula Santos_934/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Raúl_Jiménez_252/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Joe_Rodon_1036/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Martin_Ødegaard_13/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Patrick_Bamford_1170/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Mattéo_Guendouzi_1293/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Florian_Lejeune_1663/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/20

Updated Fantasy-Premier-League/data/2020-21/players/MID_Marcus_Rashford_385/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Ben_Davies_484/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_James_McCarthy_1590/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Reece_James_172/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Willy_Caballero_1244/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Ederson_Santana de Moraes_347/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Anwar_El Ghazi_1071/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Ciaran_Clark_1215/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Matt_Macey_883/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Harvey_Elliott_319/gw.csv

Updated Fantasy-Premier-League/data/2020-21/players/DEF_Javier_Manquillo Gaitán_950/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Cole_Palmer_182/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Jamal_Lewis_408/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Dwight_McNeil_230/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Jack_Grealish_349/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Adam_Forshaw_1163/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Victor_Lindelöf_376/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Anthony_Martial_931/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Tomáš_Souček_530/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Anthony_Gordon_398/gw.csv 

Updated Fantasy-Premier-League/data/2020-21/players/DEF_Pascal_Struijk_1172/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Luke_Cundle_540/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Taylor_Gardner-Hickman_1727/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Moise_Kean_1374/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Shkodran_Mustafi_1553/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Kyle_John_1129/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_James_Rodríguez_1368/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Ryan_Finnigan_1248/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Jayden_Bogle_995/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Joel_Ward_215/gw.csv wi

Updated Fantasy-Premier-League/data/2020-21/players/GK_Marek_Rodák_847/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Olivier_Giroud_1353/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Gabriel_Fernando de Jesus_2/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Willian José_Da Silva_1751/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/GK_Wes_Foderingham_522/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Alexandre_Jankewitz_1689/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Max_Sanders_1574/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Neil_Taylor_1558/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Gabriel_dos Santos Magalhães_3/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2020-21/players/DE

...

Updated Fantasy-Premier-League/data/2022-23/players/MID_Máximo_Perrone_921/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Konstantinos_Tsimikas_337/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Ethan_Pinnock_104/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Vitaly_Janelt_94/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/GK_Martin_Dúbravka_396/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Ayoze_Pérez_1150/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Andrew_Robertson_335/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Federico_Fernández_1214/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Rodrigo 'Rodri'_Hernandez_360/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_James_

Updated Fantasy-Premier-League/data/2022-23/players/DEF_Conor_Coady_288/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Jakub_Moder_137/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/FWD_Danny_Welbeck_148/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/GK_Tom_Heaton_374/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Bruno_Borges Fernandes_366/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Abdoulaye_Doucouré_217/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Andreas_Hoelgebaum Pereira_240/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Sergio_Reguilón_496/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/GK_José_Malheiro de Sá_554/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Lewis_O'B

Updated Fantasy-Premier-League/data/2022-23/players/MID_Steven_Alzate_738/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Pascal_Groß_125/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Amadou_Onana_233/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Will_Smallbone_471/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/FWD_John-Kymani_Gordon_821/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/FWD_Raúl_Jiménez_252/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Lucas_Torreira di Pascua_1068/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Jordan_Zemura_1079/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Adam_Webster_147/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Darko_Gyabi_1183/gw.c

Updated Fantasy-Premier-League/data/2022-23/players/MID_Tom_Cairney_243/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Harry_Wilson_259/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Sil_Swinkels_640/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Jordan_Ayew_192/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Neco_Williams_437/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/GK_Harvey_Davies_669/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/GK_Daniel_Bentley_536/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Jaidon_Anthony_61/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Odeluga_Offiah_139/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Richie_Laryea_972/gw.csv with crowds colu

Updated Fantasy-Premier-League/data/2022-23/players/FWD_Terry_Ablade_1139/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Malang_Sarr_176/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Rayan_Aït-Nouri_533/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Reiss_Nelson_10/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Aaron_Cresswell_517/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/GK_George_Shelvey_981/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Trent_Alexander-Arnold_311/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/MID_Carlos_Alcaraz Durán_450/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/DEF_Calum_Chambers_689/gw.csv with crowds column.
Updated Fantasy-Premier-League/data/2022-23/players/GK_Oliwier_Zych_641/gw

In [17]:
# Let's add season number
def add_season_to_gw(data_directory, season):
    # Extract the start year from the season folder (e.g., "2021-22" -> "2021")
    season_year = season.split("-")[0]

    players_folder = os.path.join(data_directory, season, "players")
    if not os.path.exists(players_folder):
        print(f"Players folder not found for season {season}. Exiting.")
        return

    # Process each player's gw.csv
    for player_folder in os.listdir(players_folder):
        player_folder_path = os.path.join(players_folder, player_folder)
        gw_file_path = os.path.join(player_folder_path, "gw.csv")
        
        if os.path.exists(gw_file_path):
            try:
                # Load player's gw.csv
                gw_data = pd.read_csv(gw_file_path)

                # Add the season column
                gw_data['season'] = int(season_year)

                # Save the updated gw.csv
                gw_data.to_csv(gw_file_path, index=False)
                print(f"Updated {gw_file_path} with season column.")
            except Exception as e:
                print(f"Error processing {gw_file_path}: {e}")

                    
data_directory = "Fantasy-Premier-League/data"
seasons = ["2020-21", "2021-22", "2022-23", "2023-24", "2024-25"]

for season in seasons:
    print(f"Processing season: {season}")
    add_season_to_gw(data_directory, season)

Processing season: 2020-21
Updated Fantasy-Premier-League/data/2020-21/players/GK_Mathew_Ryan_1329/gw.csv with season column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Marcos_Rojo_1657/gw.csv with season column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Frederico_Rodrigues de Paula Santos_934/gw.csv with season column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Raúl_Jiménez_252/gw.csv with season column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Joe_Rodon_1036/gw.csv with season column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Martin_Ødegaard_13/gw.csv with season column.
Updated Fantasy-Premier-League/data/2020-21/players/FWD_Patrick_Bamford_1170/gw.csv with season column.
Updated Fantasy-Premier-League/data/2020-21/players/MID_Mattéo_Guendouzi_1293/gw.csv with season column.
Updated Fantasy-Premier-League/data/2020-21/players/DEF_Florian_Lejeune_1663/gw.csv with season column.
Updated Fantasy-Premier-League/data/20

In [ ]:
# Finally - let's make csv with players from each position for each season
def process_season_for_positions(data_directory, season):
    """
    Process a single season to create position-specific CSVs for players.

    Args:
        data_directory (str): Base directory containing the season data.
        season (str): Season name (e.g., "2022-23").

    Returns:
        None
    """
    # Players folder path
    players_folder = os.path.join(data_directory, season, "players")
    if not os.path.exists(players_folder):
        print(f"Players folder not found for season {season}. Skipping.")
        return

    season_year = season.split("-")[0]

    def_df = pd.DataFrame()
    mid_df = pd.DataFrame()
    fwd_df = pd.DataFrame()
    gk_df = pd.DataFrame()

    # Iterate through player directories
    for player_folder in os.listdir(players_folder):
        # Extract position from folder name
        position = player_folder.split("_")[0]

        # Read the player's gw.csv
        player_folder_path = os.path.join(players_folder, player_folder)
        gw_file_path = os.path.join(player_folder_path, "gw.csv")

        if os.path.exists(gw_file_path):
            try:
                # Load gw.csv and add position and season columns
                gw_data = pd.read_csv(gw_file_path)

                # Append to the respective DataFrame
                if position == "DEF":
                    def_df = pd.concat([def_df, gw_data], ignore_index=True)
                elif position == "MID":
                    mid_df = pd.concat([mid_df, gw_data], ignore_index=True)
                elif position == "FWD":
                    fwd_df = pd.concat([fwd_df, gw_data], ignore_index=True)
                elif position == "GK":
                    gk_df = pd.concat([gk_df, gw_data], ignore_index=True)
            except Exception as e:
                print(f"Error processing {gw_file_path}: {e}")

    # Save combined CSV for each position
    output_folder = os.path.join(data_directory, season)
    os.makedirs(output_folder, exist_ok=True)

    if not def_df.empty:
        def_df.to_csv(os.path.join(output_folder, "DEF_players.csv"), index=False)
        print(f"Saved DEF players for season {season}.")
    if not mid_df.empty:
        mid_df.to_csv(os.path.join(output_folder, "MID_players.csv"), index=False)
        print(f"Saved MID players for season {season}.")
    if not fwd_df.empty:
        fwd_df.to_csv(os.path.join(output_folder, "FWD_players.csv"), index=False)
        print(f"Saved FWD players for season {season}.")
    if not gk_df.empty:
        gk_df.to_csv(os.path.join(output_folder, "GK_players.csv"), index=False)
        print(f"Saved GK players for season {season}.")

data_directory = "Fantasy-Premier-League/data"
seasons = ["2020-21", "2021-22", "2022-23", "2023-24", "2024-25"]

for season in seasons:
    print(f"Processing season: {season}")
    process_season_for_positions(data_directory, season)

Processing season: 2020-21
Saved DEF players for season 2020-21.
Saved MID players for season 2020-21.
Saved FWD players for season 2020-21.
Saved GK players for season 2020-21.
Processing season: 2021-22
